In [1]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.gaussian_process import GaussianProcessClassifier


from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.metrics import classification_report

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import IncrementalPCA

In [2]:
from sklearn.metrics import classification_report
import os
import pickle
import numpy as np

In [3]:
class autolabel:

    def __init__(self, clf_path, survey_path, mode, parameters):
        if clf_path.endswith('/'):
            self.clf_path = clf_path
        else:
            self.clf_path = clf_path + '/'
        
        self.clf_path = clf_path
        self.survey_path = survey_path
        self.mode = mode
        self.parameters = parameters
        self.clf = None
        self.report = None
        
    def initialize_classifier(self):
        params = self.parameters

        path = self.clf_path

        clf_name = params["name"]
        report = 'analysis_report'
        test_data = 'testing'
        train_data = 'training'

        clfnew = path + '/' + clf_name

        report_folder = clfnew + '/' + report
        test_folder = clfnew + '/' + test_data
        train_folder = clfnew + '/' + train_data

        clf_folders = (clfnew, report_folder, test_folder, train_folder)

        for elem in clf_folders:
            try:
                os.mkdir(elem)
            except:
                pass

        if params['classifier'] == 'Gaussian Process':
            clfr = GaussianProcessClassifier()
            
        elif params['classifier'] == 'Random Forest':
            clfr = RandomForestClassifier()
            
        elif params['classifier'] == 'MLP':
            clfr = MLPClassifier()
            
        else:
            raise Exception(
                "Classifier type must be {'Gaussian Process', 'Random Forest', or 'MLP'}")
        
        clf = GridSearchCV(clfr, params['clf_params'],scoring = 'balanced_accuracy')
        pipe = Pipeline([('scaler', StandardScaler()),
                             ('transformer', IncrementalPCA(n_components = 1, whiten = True)), ('learner', clf)])
        
        try:
            with open(clfnew  + '/init_clf.pickle','wb') as f:
                pickle.dump(pipe, f, pickle.HIGHEST_PROTOCOL)
        except:
            pass
        
        return pipe
    
    
    
    def train(self):
        
        params = self.parameters
        
        clf_name = params["name"]
        path = self.clf_path
        clf_path = path + clf_name + '/init_clf.pickle'
        clf = pickle.load( open( clf_path, "rb" ) )
        
        
        if type(self.survey_path) == str:
            features = np.load(self.survey_path + '/resolution' + str(params["resolution"]) + '/2_rawtexturefeatures/features.npy')
        
        elif type(self.survey_path) == list:
            
            feature_list = []
            
            for path in self.survey_path:
                features = np.load(path + '/resolution' + str(params["resolution"]) + '/2_rawtexturefeatures/features.npy')
                feature_list.append(features)

            features = np.concatenate(tuple(feature_list),axis = 0)
        
        clean_features = features[~np.isnan(features).any(axis=1)]
        cf = clean_features[clean_features[:,4] != 0]
        
        # print(cf.shape)
        # print("features shape:", features.shape)
        feat_train, feat_test, label_train, label_test = train_test_split( 
            np.nan_to_num(cf[:,[3,5]]), np.nan_to_num(cf[:,4]), test_size=0.33, random_state=97)
        
        
        path = self.clf_path

        clf_name = params["name"]
        report = 'analysis_report'
        test_data = 'testing'
        train_data = 'training'

        clfnew = path + clf_name

        report_folder = clfnew + '/' + report
        test_folder = clfnew + '/' + test_data
        train_folder = clfnew + '/' + train_data
        
        try:
            np.savez(train_folder + '/training.npz' ,features = feat_train, labels = label_train)
            np.savez(test_folder + '/testing.npz' ,features = feat_test, labels = label_test)
        except:
            pass
        
        clf.fit(feat_train,label_train)
        
        self.clf = clf
        
        
        # print(label_test[0].shape, clf.predict(feat_test[0]).shape)
        
        try:
            target_names = ['unclassified', 'water']
            self.report = classification_report(label_test, heregoes.clf.predict(feat_test), output_dict = True, target_names = target_names)
        except:
            pass

In [4]:
clfolder = 'C:/Users/nivan/Desktop/Beach 2020/classifiers'

dataloc = 'C:/Users/nivan/Desktop/Beach 2020/20190327_00568_00622_NoFilters_Torrey_DelMar'

mode = 1


mlp_params = {
    "hidden_layer_sizes" : ((80,),(100,),(120,)),
    "activation" : ('logistic','tanh','relu'),
    "solver" : ('lbfgs','sgd','adam'),
    "learning_rate" : ('constant','adaptive'),
    "max_iter" : [200,300,500],
    "random_state" : [0,42,97],
    "tol" : [1e-4, 5e-5],
    "verbose" : [True],
    "warm_start" : [True]
}

parameters = {
    "classifier" : 'MLP',
    "resolution" : 1,
    "name" : 'MLP_test1',
    'clf_params' : mlp_params
}


heregoes = autolabel(clfolder, dataloc , mode, parameters)

In [5]:
heregoes.initialize_classifier()

Pipeline(memory=None,
     steps=[('scaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('transformer', IncrementalPCA(batch_size=None, copy=True, n_components=1, whiten=True)), ('learner', GridSearchCV(cv='warn', error_score='raise-deprecating',
       estimator=MLPClassifier(activation='relu', alpha=0.0001, ...='2*n_jobs', refit=True, return_train_score='warn',
       scoring='balanced_accuracy', verbose=0))])

In [6]:
heregoes.train()

(4016, 21)
features shape: (4016, 21)


C:\Users\nivan\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)


Iteration 1, loss = 0.52647582
Iteration 2, loss = 0.37618630
Iteration 3, loss = 0.25595408
Iteration 4, loss = 0.18660198
Iteration 5, loss = 0.14924462
Iteration 6, loss = 0.12786254
Iteration 7, loss = 0.11485470
Iteration 8, loss = 0.10585739
Iteration 9, loss = 0.09976657
Iteration 10, loss = 0.09520604
Iteration 11, loss = 0.09164507
Iteration 12, loss = 0.08879518
Iteration 13, loss = 0.08647697
Iteration 14, loss = 0.08464782
Iteration 15, loss = 0.08300706
Iteration 16, loss = 0.08165248
Iteration 17, loss = 0.08052084
Iteration 18, loss = 0.07957971
Iteration 19, loss = 0.07869311
Iteration 20, loss = 0.07793939
Iteration 21, loss = 0.07727279
Iteration 22, loss = 0.07667605
Iteration 23, loss = 0.07616798
Iteration 24, loss = 0.07572404
Iteration 25, loss = 0.07530392
Iteration 26, loss = 0.07493890
Iteration 27, loss = 0.07458851
Iteration 28, loss = 0.07428797
Iteration 29, loss = 0.07404781
Iteration 30, loss = 0.07378103
Iteration 31, loss = 0.07356066
Iteration 32, los

Iteration 1, loss = 0.52694094
Iteration 2, loss = 0.37642728
Iteration 3, loss = 0.25543148
Iteration 4, loss = 0.18679287
Iteration 5, loss = 0.14940148
Iteration 6, loss = 0.12772293
Iteration 7, loss = 0.11460315
Iteration 8, loss = 0.10594395
Iteration 9, loss = 0.09984941
Iteration 10, loss = 0.09518241
Iteration 11, loss = 0.09155736
Iteration 12, loss = 0.08879395
Iteration 13, loss = 0.08644136
Iteration 14, loss = 0.08459076
Iteration 15, loss = 0.08304479
Iteration 16, loss = 0.08170079
Iteration 17, loss = 0.08053008
Iteration 18, loss = 0.07954708
Iteration 19, loss = 0.07867475
Iteration 20, loss = 0.07796117
Iteration 21, loss = 0.07724828
Iteration 22, loss = 0.07668445
Iteration 23, loss = 0.07616934
Iteration 24, loss = 0.07573846
Iteration 25, loss = 0.07532401
Iteration 26, loss = 0.07494249
Iteration 27, loss = 0.07457564
Iteration 28, loss = 0.07429127
Iteration 29, loss = 0.07404720
Iteration 30, loss = 0.07380043
Iteration 31, loss = 0.07355483
Iteration 32, los

Iteration 2, loss = 0.38143025
Iteration 3, loss = 0.28973162
Iteration 4, loss = 0.22598779
Iteration 5, loss = 0.18320144
Iteration 6, loss = 0.15416943
Iteration 7, loss = 0.13433968
Iteration 8, loss = 0.11983717
Iteration 9, loss = 0.10961569
Iteration 10, loss = 0.10190947
Iteration 11, loss = 0.09592750
Iteration 12, loss = 0.09122397
Iteration 13, loss = 0.08743878
Iteration 14, loss = 0.08450886
Iteration 15, loss = 0.08194779
Iteration 16, loss = 0.07986330
Iteration 17, loss = 0.07816225
Iteration 18, loss = 0.07676361
Iteration 19, loss = 0.07549338
Iteration 20, loss = 0.07442284
Iteration 21, loss = 0.07348028
Iteration 22, loss = 0.07266103
Iteration 23, loss = 0.07198439
Iteration 24, loss = 0.07137602
Iteration 25, loss = 0.07082172
Iteration 26, loss = 0.07034439
Iteration 27, loss = 0.06988879
Iteration 28, loss = 0.06948490
Iteration 29, loss = 0.06917519
Iteration 30, loss = 0.06882631
Iteration 31, loss = 0.06854500
Iteration 32, loss = 0.06826210
Iteration 33, lo

...

Iteration 55, loss = 0.10410423
Iteration 56, loss = 0.10297468
Iteration 57, loss = 0.10193574
Iteration 58, loss = 0.10087653
Iteration 59, loss = 0.09990482
Iteration 60, loss = 0.09898855
Iteration 61, loss = 0.09808473
Iteration 62, loss = 0.09719802
Iteration 63, loss = 0.09637901
Iteration 64, loss = 0.09560789
Iteration 65, loss = 0.09483140
Iteration 66, loss = 0.09410672
Iteration 67, loss = 0.09340906
Iteration 68, loss = 0.09272263
Iteration 69, loss = 0.09206447
Iteration 70, loss = 0.09144177
Iteration 71, loss = 0.09083969
Iteration 72, loss = 0.09024827
Iteration 73, loss = 0.08970194
Iteration 74, loss = 0.08916922
Iteration 75, loss = 0.08863119
Iteration 76, loss = 0.08813568
Iteration 77, loss = 0.08763892
Iteration 78, loss = 0.08717410
Iteration 79, loss = 0.08672254
Iteration 80, loss = 0.08628748
Iteration 81, loss = 0.08585458
Iteration 82, loss = 0.08545193
Iteration 83, loss = 0.08505890
Iteration 84, loss = 0.08466203
Iteration 85, loss = 0.08430502
Iteratio

Iteration 60, loss = 0.09921864
Iteration 61, loss = 0.09830892
Iteration 62, loss = 0.09742985
Iteration 63, loss = 0.09661560
Iteration 64, loss = 0.09582712
Iteration 65, loss = 0.09507552
Iteration 66, loss = 0.09432793
Iteration 67, loss = 0.09365088
Iteration 68, loss = 0.09296725
Iteration 69, loss = 0.09231427
Iteration 70, loss = 0.09169307
Iteration 71, loss = 0.09107823
Iteration 72, loss = 0.09051159
Iteration 73, loss = 0.08994586
Iteration 74, loss = 0.08942633
Iteration 75, loss = 0.08889762
Iteration 76, loss = 0.08839397
Iteration 77, loss = 0.08791139
Iteration 78, loss = 0.08744067
Iteration 79, loss = 0.08700652
Iteration 80, loss = 0.08655986
Iteration 81, loss = 0.08613616
Iteration 82, loss = 0.08573298
Iteration 83, loss = 0.08533855
Iteration 84, loss = 0.08496719
Iteration 85, loss = 0.08458699
Iteration 86, loss = 0.08424156
Iteration 87, loss = 0.08389338
Iteration 88, loss = 0.08354781
Iteration 89, loss = 0.08323913
Iteration 90, loss = 0.08290592
Iteratio

Iteration 61, loss = 0.06372382
Iteration 62, loss = 0.06356761
Iteration 63, loss = 0.06342300
Iteration 64, loss = 0.06328854
Iteration 65, loss = 0.06315571
Iteration 66, loss = 0.06303858
Iteration 67, loss = 0.06293520
Iteration 68, loss = 0.06284426
Iteration 69, loss = 0.06275515
Iteration 70, loss = 0.06269411
Iteration 71, loss = 0.06263399
Iteration 72, loss = 0.06249874
Iteration 73, loss = 0.06244099
Iteration 74, loss = 0.06244795
Iteration 75, loss = 0.06237127
Iteration 76, loss = 0.06226235
Iteration 77, loss = 0.06224197
Iteration 78, loss = 0.06222386
Iteration 79, loss = 0.06216198
Iteration 80, loss = 0.06209003
Iteration 81, loss = 0.06204439
Iteration 82, loss = 0.06201225
Iteration 83, loss = 0.06200532
Iteration 84, loss = 0.06198349
Iteration 85, loss = 0.06196144
Iteration 86, loss = 0.06192033
Iteration 87, loss = 0.06192168
Training loss did not improve more than tol=0.000100 for 10 consecutive epochs. Stopping.
Iteration 1, loss = 0.77186550
Iteration 2, lo

Iteration 79, loss = 0.06216198
Iteration 80, loss = 0.06209003
Iteration 81, loss = 0.06204439
Iteration 82, loss = 0.06201225
Iteration 83, loss = 0.06200532
Iteration 84, loss = 0.06198349
Iteration 85, loss = 0.06196144
Iteration 86, loss = 0.06192033
Iteration 87, loss = 0.06192168
Iteration 88, loss = 0.06186796
Iteration 89, loss = 0.06186945
Iteration 90, loss = 0.06184387
Iteration 91, loss = 0.06179126
Iteration 92, loss = 0.06180279
Iteration 93, loss = 0.06176911
Iteration 94, loss = 0.06173315
Iteration 95, loss = 0.06171923
Iteration 96, loss = 0.06173442
Iteration 97, loss = 0.06170978
Iteration 98, loss = 0.06168806
Iteration 99, loss = 0.06167807
Iteration 100, loss = 0.06166105
Iteration 101, loss = 0.06171400
Iteration 102, loss = 0.06164703
Training loss did not improve more than tol=0.000050 for 10 consecutive epochs. Stopping.
Iteration 1, loss = 0.77186550
Iteration 2, loss = 0.69152655
Iteration 3, loss = 0.61885747
Iteration 4, loss = 0.55465429
Iteration 5, lo

C:\Users\nivan\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [8]:
heregoes.report

{'unclassified': {'precision': 0.9849170437405732,
  'recall': 1.0,
  'f1-score': 0.9924012158054711,
  'support': 1306},
 'water': {'precision': 0.0, 'recall': 0.0, 'f1-score': 0.0, 'support': 20},
 'micro avg': {'precision': 0.9849170437405732,
  'recall': 0.9849170437405732,
  'f1-score': 0.9849170437405732,
  'support': 1326},
 'macro avg': {'precision': 0.4924585218702866,
  'recall': 0.5,
  'f1-score': 0.49620060790273557,
  'support': 1326},
 'weighted avg': {'precision': 0.97006158305067,
  'recall': 0.9849170437405732,
  'f1-score': 0.9774328716756752,
  'support': 1326}}

In [9]:
test = np.load('C:/Users/nivan/Desktop/Beach 2020/classifiers/MLP_test1/testing/delmar.npz')

In [10]:
np.unique(test['labels'])

array([1., 2.])